In [1]:
import pandas as pd
import numpy as np

import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

pd.options.display.float_format = '{:,.3f}'.format

In [2]:
# Mount data from drive
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


#1 Analisis espectral de señales

## 1.1. Descripción de las variables



*   **DL_Traffic:** Volumen de tráfico enviado desde la red a los clientes [MBytes]
*   **User_Active_DL_Avg:** Cantidad de clientes activos promedios. Estos clientes son los que se encuentran traficando, a diferencia de un cliente conectado que es aquel que el telefono si bien esta conectado no se encuentra en actividad.
* **Throughput_User_Dl:** Velocidad de bajada promedio por usuario 



In [3]:
from numpy.fft import fft, ifft

## 1.2 Carga dataset

In [4]:
path_file='/content/drive/MyDrive/maestria/materias/Series temporales/TP_2/dataset.csv'

df = pd.read_csv(path_file,sep=';') 
df.rename(columns = {'PERIOD_START_TIME':'timepo_15min'}, inplace = True)
df.drop(columns=['LNCEL_NAME'],inplace=True)
#Convierto el tiempo en el tipo de variable datetime
df['timepo_15min'] = pd.to_datetime(df['timepo_15min'], dayfirst = True) 
print(df.dtypes)
# Lo pongo como indice
df.set_index("timepo_15min", inplace=True)
# Geenra un eje temporal sin huecos
df=df.asfreq(freq='15min',method='ffill')

timepo_15min          datetime64[ns]
DL_Traffic                   float64
User_Active_DL_Avg           float64
Throughput_User_Dl           float64
dtype: object


In [5]:
df['split']='train'
df['split'].iloc[len(df)-24*4:]='test'

/usr/local/lib/python3.8/dist-packages/pandas/core/indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


## 1.3 Generacion de series sintetizadas

Se definirán dos funciones para la sintetizacion de series periódicas

In [6]:
def quickStart(df_xn,N_tot,nro_comp_espect=50, fm=24*4):
  #########################################################################################################################
  # Esta funcion genera:                                                                                                  #
  #     - los ejes de frecuencia para la secuencia original y para la ampliada (N_tot)                                    #
  #     - el eje temporal para ambas secuencias                                                                           #
  #     - genera una grafica de componenetes espectrales para ver donde cortar                      
  #  
  # df_xn: serie a trabajar, generalmente son los datos de train
  # N_tot: tamaño final de la serie, generalemnte es train + test
  # nro_comp_espect: son la cantidad de frecuencias a graficar
  # fm: cantidad de muestras en el día                                        #
  #########################################################################################################################    

  #muestras por días
  Tm=1/fm
  # T=1 # periodo de la serie, cada 7 dias
  N=df_xn.shape[0] # Tamaño de la serie original, generalmente de Train

  #---------------------------------------------------------
  # EJES TEMPORALES
  n=np.arange(0,N)
  n_tot=np.arange(0,N_tot)

  # Ejes de frecuencias - train
  k=np.concatenate([np.arange(0,N/2), np.arange(-N/2,0)]) # La funcion fft da las frecuences 0 a fn y -fn a 0 siendo fn la frecuencia de Nyquist
  k=np.concatenate([np.arange(0,N/2), np.arange(-N/2,0)]) # La funcion fft da las frecuences 0 a fn y -fn a 0 siendo fn la frecuencia de Nyquist
  s=k/N*fm 

  # Ejes de frecuencias -pra la salida generalmente train + test
  N_tot=df.shape[0]
  k_tot=np.concatenate([np.arange(0,N_tot/2), np.arange(-N_tot/2,0)]) # La funcion fft da las frecuences 0 a fn y -fn a 0 siendo fn la frecuencia de Nyquist
  k_tot=np.concatenate([np.arange(0,N_tot/2), np.arange(-N_tot/2,0)]) # La funcion fft da las frecuences 0 a fn y -fn a 0 siendo fn la frecuencia de Nyquist
  s_tot=k_tot/N_tot*fm

  #-----------------------------------------------------------
  # Transformada de Fourier para buscar armonicos
  df_Xf = fft(df_xn)/N 

  X_codo=pd.DataFrame(abs(df_Xf)**2,columns=['modulo2'])
  X_codo['real']=np.real(df_Xf)
  X_codo['imag']=np.imag(df_Xf)
  X_codo['freq']=s

  df_codo=X_codo.sort_values(by='modulo2',ascending=False)['modulo2'].head(50).reset_index()
  fig = px.line(df_codo, x=df_codo.index, y='modulo2', markers=True)
  fig.show()

  return n,n_tot,s,s_tot
  

In [7]:
def get_series(df_xn,s,N_tot,nro_comp_espect=1, fm=24*4):
  Tm=1/fm
  N=df_xn.shape[0]
  #-----------------------------------------------------------
  # Transformada de Fourier para buscar armonicos
  df_Xf = fft(df_xn)/N 

  n_tot=np.arange(0,N_tot)
  zn=np.zeros(N_tot) # N_tot tiene el largo de la serie completa

  X_codo=pd.DataFrame(abs(df_Xf)**2,columns=['modulo2'])
  X_codo['real']=np.real(df_Xf)
  X_codo['imag']=np.imag(df_Xf)
  X_codo['freq']=s

  df_codo=X_codo.sort_values(by='modulo2',ascending=False)['modulo2'].reset_index()

  # Serie de Fourier, contruccion de la serie sintetica
  for i,inx in enumerate(df_codo.head(nro_comp_espect)['index']):
    if i%2==0:
      # print(inx)
      reali=X_codo.loc[inx,'real']
      imagi=X_codo.loc[inx,'imag']
      fi=X_codo.loc[inx,'freq']
      zn=zn + 2*(reali*np.cos(2*np.pi*n_tot*Tm*fi)-imagi*np.sin(2*np.pi*n_tot*Tm*fi))

  # Se realiza la transformada de Forurier de la serie sintetizada
  Z_f = fft(zn)/N_tot
  return zn,Z_f

### 1.3.1 Tráfico

In [8]:
traffic_mu_train=df[df['split']=='train']['DL_Traffic'].mean() 
x_n_traffic=df[df['split']=='train']['DL_Traffic']-traffic_mu_train # Se utiliza sin 

# Se realiza la Transformada de Fourier de la serie de entrada
N=x_n_traffic.shape[0]
X_f_traffic = fft(x_n_traffic)/N

In [9]:
n,n_tot,s,s_tot=quickStart(x_n_traffic,x_n_traffic.shape[0])

In [10]:
# Se encuentra la serie sintetizada y su transformada
z_n_traff,Z_f_traff=get_series(x_n_traffic,s,df.shape[0],nro_comp_espect=16)

In [11]:
fig = make_subplots(rows=2, cols=2)

original=X_f_traffic #Serie de train
sintetizada=Z_f_traff #Serie generada sinteticamente con un largo total (train+test)

fig.add_trace(go.Scatter(x=s, y=np.real(original), mode='lines', name='Real de X(f)'),row=1, col=1)
fig.add_trace(go.Scatter(x=s, y=np.imag(original),mode='lines',name='Imag de X(f)'),row=1, col=2)

# Sintetizado
fig.add_trace(go.Scatter(x=s_tot, y=np.real(sintetizada), mode='lines', name='Real de Z(f)'),row=2, col=1)
fig.add_trace(go.Scatter(x=s_tot, y=np.imag(sintetizada),mode='lines',name='Imag de Z(f)'),row=2, col=2)

fig.update_layout(height=600, width=1000, title_text="Análisis espectral ",legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1))
fig.update_xaxes(range=[-5, 5])
fig.show()

Se observa que el comportamiento espectral es similar. Si ahora observamos el comportamiento en el tiempo nos dará el siguiente gráfico

In [12]:
df['trafico_sint']=z_n_traff+ traffic_mu_train #Le agregamos la media que sacamos para el analisis espectral

In [13]:
fig = go.Figure()

sintetizada=df['trafico_sint']
original=df['DL_Traffic'] # Aca si se pone toda la serie completa (Entrenamiento mas test a fin de comparar)


fig.add_trace(go.Scatter(x=df['DL_Traffic'].index, y=original,mode='lines',yaxis='y1',name="Original"))
fig.add_trace(go.Scatter(x=original.index, y=sintetizada,mode='lines',yaxis='y1',name="Sintetizada"))
fig.update_layout(height=500, width=1000, title_text='Trafico',yaxis=dict(title="Original axis"),
                  legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1))
fig.show()

Debido a que se sabe que el trafico no puede ser negativo se realiza una correccion a la serie

In [14]:
# df['trafico_sint']=df['trafico_sint'].map(lambda x:0 if x<0 else x)

### 1.3.2 Usuarios

In [15]:
usuarios_mu_train=df[df['split']=='train']['User_Active_DL_Avg'].mean() 
x_n_usuarios=df[df['split']=='train']['User_Active_DL_Avg']-usuarios_mu_train

X_f_usuarios = fft(x_n_usuarios)/N

n,n_tot,s,s_tot=quickStart(x_n_usuarios,x_n_usuarios.shape[0])

In [16]:
z_n_user,Z_f_user=get_series(x_n_usuarios,s,df.shape[0],nro_comp_espect=20)

In [17]:
fig = make_subplots(rows=2, cols=2)

original=X_f_usuarios #Serie de train
sintetizada=Z_f_user #Serie generada sinteticamente con un largo total (train+test)

fig.add_trace(go.Scatter(x=s, y=np.real(original), mode='lines', name='Real de X(f)'),row=1, col=1)
fig.add_trace(go.Scatter(x=s, y=np.imag(original),mode='lines',name='Imag de X(f)'),row=1, col=2)

# Sintetizado
fig.add_trace(go.Scatter(x=s_tot, y=np.real(sintetizada), mode='lines', name='Real de Z(f)'),row=2, col=1)
fig.add_trace(go.Scatter(x=s_tot, y=np.imag(sintetizada),mode='lines',name='Imag de Z(f)'),row=2, col=2)

fig.update_layout(height=600, width=1000, title_text="Análisis espectral ",legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1))
fig.update_xaxes(range=[-5, 5])
fig.show()

In [18]:
df['user_sint']=z_n_user+ usuarios_mu_train #Le agregamos la media que sacamos para el analisis espectral

In [19]:
# df['user_sint']=df['user_sint'].map(lambda x:0 if x<0 else x)

In [20]:
fig = go.Figure()

sintetizada=df['user_sint']
original=df['User_Active_DL_Avg'] # Aca si se pone toda la serie completa (Entrenamiento mas test a fin de comparar)


fig.add_trace(go.Scatter(x=df['User_Active_DL_Avg'].index, y=original,mode='lines',yaxis='y1',name="Original"))
fig.add_trace(go.Scatter(x=original.index, y=sintetizada,mode='lines',yaxis='y1',name="Sintetizada"))
fig.update_layout(height=500, width=1000, title_text='Usuarios',yaxis=dict(title="Original axis"),
                  legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1))
fig.show()

Debido a que se sabe que los usuarios no puede ser menor a cero se le realiza una correccion a la serie sintetizada

### 1.3.3 Throughput

In [21]:
thp_mu_train=df[df['split']=='train']['Throughput_User_Dl'].mean() 
x_n_thp=df[df['split']=='train']['Throughput_User_Dl']-thp_mu_train

X_f_thp = fft(x_n_thp)/N

n,n_tot,s,s_tot=quickStart(x_n_thp,x_n_thp.shape[0])

In [22]:
z_n_thp,Z_f_thp=get_series(x_n_thp,s,df.shape[0],nro_comp_espect=26)

In [23]:
fig = make_subplots(rows=2, cols=2)

original=X_f_thp #Serie de train
sintetizada=Z_f_thp #Serie generada sinteticamente con un largo total (train+test)

fig.add_trace(go.Scatter(x=s, y=np.real(original), mode='lines', name='Real de X(f)'),row=1, col=1)
fig.add_trace(go.Scatter(x=s, y=np.imag(original),mode='lines',name='Imag de X(f)'),row=1, col=2)

# Sintetizado
fig.add_trace(go.Scatter(x=s_tot, y=np.real(sintetizada), mode='lines', name='Real de Z(f)'),row=2, col=1)
fig.add_trace(go.Scatter(x=s_tot, y=np.imag(sintetizada),mode='lines',name='Imag de Z(f)'),row=2, col=2)

fig.update_layout(height=600, width=1000, title_text="Análisis espectral ",legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1))
fig.update_xaxes(range=[-5, 5])
fig.show()

In [24]:
df['thp_sint']=z_n_thp+ thp_mu_train #Le agregamos la media que sacamos para el analisis espectral

In [25]:
fig = go.Figure()

sintetizada=df['thp_sint']
original=df['Throughput_User_Dl'] # Aca si se pone toda la serie completa (Entrenamiento mas test a fin de comparar)


fig.add_trace(go.Scatter(x=df['Throughput_User_Dl'].index, y=original,mode='lines',yaxis='y1',name="Original"))
fig.add_trace(go.Scatter(x=original.index, y=sintetizada,mode='lines',yaxis='y1',name="Sintetizada"))
fig.update_layout(height=500, width=1000, title_text='Throughput',yaxis=dict(title="Original axis"),
                  legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1))
fig.show()